  ### What is an Ensemble?

First, we need to understand what an ensemble is and how it is structured. In the HEFS API, for a given location ID and parameter ID, a forecast ensemble is a set of forecast time series (ensemble members). Each ensemble member consists of a series of timestep values with a coresponding forecasted value.

  ### Retrieving Data from the API

We need a way to retrieve the data from the API. To achieve this, we first import Python's requests library, which allows us to make HTTP requests. Additionally, we import the pprint function from the pprint library to make the output more readable. Finally, we define the API endpoint we'll be interacting with, setting API_ENDPOINT to https://api.water.noaa.gov/hefs/. Here's how we do it:

In [ ]:
# start by importing the requests library
import requests
# import the pprint library to make the output more readable
from pprint import pprint
# define the api-endpoint
API_ENDPOINT = "https://api.water.noaa.gov/hefs"
LOCATION_ID = "RUPM8"
PARAMETER_ID = "QINE"

### Most Recent Ensemble Forecast for a Location and Plotting

In other cases, you might want to retrieve and plot recent ensemble data. The API, unless otherwise specified via a specific date request, will return the most recent ensemble.

For example, to retrieve the latest QINE ensemble forecast for location id RUPM8, you'll specify `location_id=RUPM8`, `parameter_id=QINE`, and `limit=1`.  

`/v1/ensembles/?location_id={LOCATION_ID}&parameter_id={PARAMETER_ID}&limit=1`

Where LOCATION_ID and PARAMETER_ID are the location id and parameter id of the request respectively.

In [ ]:
from datetime import datetime, timedelta
# create a series request with location_id, parameter_id, and ordering filters
uri = API_ENDPOINT + f"/v1/ensembles/?location_id={LOCATION_ID}&parameter_id={PARAMETER_ID}&limit=1"
# get the response
response = requests.request("GET", uri)
# print the response
pprint(response.json())

We now use the data above to plot the ensemble forecast. To do this, we must parse through the response data and plot each ensemble member's data points (time/value pairs) onto a single graph.  We will use the matplotlib python package to plot the data.

In [ ]:
import matplotlib.pyplot as plt
import datetime

def graph_ensemble_data(response_data):
  """Graphs ensemble data from a API response.

  Args:
    response_data: A dictionary containing the API response data.
  """
  if response_data != []:
    # iterate through result in results
    for result in response_data[0]:
      # check if event is present in response data
      if 'events' in result and result['events']:
        # iterate through event forcasts in the ensemble api response
        for event in result['events']:
          # initialize times list
          times = []
          # initialize values list
          values = []
          # iterate through values in the sepecific forcast event
          for value in result['events']:
            if value['value'] is not None and ('miss_val' not in result or value['value'] != result['miss_val']):
              # prepare datetime for reformatting
              datetime_str = f"{value['valid_datetime']}"
              datetime_str = datetime_str.replace('T', " ")
              datetime_str = datetime_str.replace('Z', "")
              # format datetime to Year-Month-Day Hour:Minutes:Seconds
              datetime_obj = datetime.datetime.strptime(datetime_str, "%Y-%m-%d %H:%M:%S")
              # add values from the forecast to their respective lists
              times.append(datetime_obj)
              values.append(float(value['value']))
          # plot the date for the event forecast
          #print("now")
          plt.plot(times, values)
  # set x graph label
  plt.xlabel('Time')
  # set y graph label
  plt.ylabel('Value')
  # set graph title
  plt.title('Ensemble Data')
  # rotate x text vertically for better visibility
  plt.xticks(rotation='vertical')
  # display the actaul plot
  plt.show()

# call graphing function
graph_ensemble_data(response.json())


## Summary

In this notebook, we learned how to use the HEFS API to retrieve the latest ensemble forecast for a given location. We also learned how to use visualize ensemble data using matplotlib.

To try the ensembles endpoint via swagger go to: https://api.water.noaa.gov/hefs/v1/docs/#/ensembles